<a href="https://colab.research.google.com/github/nishanthnandakumar/Lidar_Radar_Systems/blob/main/lidarassignment1_ipynb_txt.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np # load point clouds and more array/vector operations
import cv2 # load images
import plotly.graph_objects as go # visualize point clouds

In [2]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [3]:
root = "./gdrive/MyDrive/dataset/Record1/"

In [4]:
def inv_rot(rot):
    """
        Calculates for a given 4x4 transformation matrix (R|t) the inverse.
    """
    inv_rot_mat = np.zeros((4,4))
    inv_rot_mat[0:3,0:3] = rot[0:3,0:3].T
    inv_rot_mat[0:3,3] = -np.dot(rot[0:3,0:3].T, rot[0:3,3])
    inv_rot_mat[3,3] = 1
    return inv_rot_mat

In [5]:
def transfer_points(points, rot_t):
    """
        Calculates the transformation of a point cloud for a given transformation matrix.
    """
    points = np.concatenate([points, np.ones([1,points.shape[1]])])
    points[0:3,:] = np.dot(rot_t, points[0:4,:])[0:3, :]
    return points[0:3]

In [6]:
def make_boundingbox(label):
    """
        Calculates the Corners of a bounding box from the parameters.
    """
    corner = np.array([
        [+ label[3]/2, + label[4]/2, + label[5]/2],
        [+ label[3]/2, + label[4]/2, - label[5]/2],
        [+ label[3]/2, - label[4]/2, + label[5]/2],
        [+ label[3]/2, - label[4]/2, - label[5]/2],
        [- label[3]/2, + label[4]/2, + label[5]/2],
        [- label[3]/2, - label[4]/2, + label[5]/2],
        [- label[3]/2, + label[4]/2, - label[5]/2],
        [- label[3]/2, - label[4]/2, - label[5]/2],
    ])
    corner = transfer_points(corner.T, rt_matrix(yaw = label[6])).T
    corner = corner + label[0:3]
    return corner

In [7]:
pwd

'/content'

In [8]:
def rt_matrix(x=0, y=0, z=0, roll=0, pitch=0, yaw=0):
    """
        Calculates a 4x4 Transformation Matrix. Angels in radian!
    """
    c_y = np.cos(yaw)
    s_y = np.sin(yaw)
    c_r = np.cos(roll)
    s_r = np.sin(roll)
    c_p = np.cos(pitch)
    s_p = np.sin(pitch)
    
    rot = np.dot(np.dot(np.array([[c_y,-s_y,0],
                                     [s_y,c_y,0],
                                     [0,0,1]]),
                           np.array([[c_p,0,s_p],
                                     [0,1,0],
                                     [-s_p,0,c_p]])),
                            np.array([[1,0,0],
                                     [0,c_r,-s_r],
                                     [0,s_r,c_r]]))
    matrix = np.array([[0,0,0,x],
                     [0,0,0,y],
                     [0,0,0,z],
                     [0,0,0,1.]])
    matrix[0:3,0:3] += rot
    return matrix

In [9]:
rotationmat = np.load(root + "calibrationMat.npy")
invrotationmat = inv_rot(rotationmat)

In [10]:
ind = 19
blick = np.loadtxt(root + "Blickfeld/point_cloud/%06d.csv" % ind)
velo = np.loadtxt(root + "Velodyne/point_cloud/%06d.csv" % ind)
velo = transfer_points(velo.T[0:3], rotationmat).T

bb = np.loadtxt(root + "/Blickfeld/bounding_box/%06d.csv" % ind)
bb = make_boundingbox(bb)

In [11]:
bb[:,0]

array([2.15781636, 2.15781636, 2.15781636, 2.15781636, 0.21781636,
       0.21781636, 0.21781636, 0.21781636])

In [12]:
data = [go.Scatter3d(x = blick[:,0],
                     y = blick[:,1],
                     z = blick[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(blick.shape[0]),
                    marker={
                        'size': 2,
                        'color': "blue",
                        'colorscale':'rainbow',
}),
        
        go.Scatter3d(x = bb[:,0],
                     y = bb[:,1],
                     z = bb[:,2],
                     text=np.arange(8),
                    mode='markers', type='scatter3d',
                    marker={
                        'size': 2,
                        'color': "red",
                        'colorscale':'rainbow',
})
]
layout = go.Layout(
    scene={
        'xaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'yaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'zaxis': {'range': [-25, 25], 'rangemode': 'tozero'}
    }
)
go.Figure(data=data, layout = layout)

In [13]:
ind = 19
blick = np.loadtxt(root + "Blickfeld/point_cloud/%06d.csv" % ind)
velo = np.loadtxt(root + "Velodyne/point_cloud/%06d.csv" % ind)
blick = transfer_points(blick.T[0:3], invrotationmat).T

bb = np.loadtxt(root + "/Velodyne/bounding_box/%06d.csv" % ind)
bb = make_boundingbox(bb)

In [14]:
data = [go.Scatter3d(x = blick[:,0],
                     y = blick[:,1],
                     z = blick[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(blick.shape[0]),
                    marker={
                        'size': 2,
                        'color': "blue",
                        'colorscale':'rainbow',
}),
        go.Scatter3d(x = velo[:,0],
                     y = velo[:,1],
                     z = velo[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(velo.shape[0]),
                    marker={
                        'size': 2,
                        'color': "green",
                        'colorscale':'rainbow',
}),
        go.Scatter3d(x = bb[:,0],
                     y = bb[:,1],
                     z = bb[:,2],
                     text=np.arange(8),
                    mode='markers', type='scatter3d',
                    marker={
                        'size': 2,
                        'color': "red",
                        'colorscale':'rainbow',
})
]
layout = go.Layout(
    scene={
        'xaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'yaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'zaxis': {'range': [-25, 25], 'rangemode': 'tozero'}
    }
)
go.Figure(data=data, layout = layout)

In [15]:
root = "./gdrive/MyDrive/dataset/Record2/"

In [16]:
rotationmat = np.load(root + "calibrationMat.npy")
invrotationmat = inv_rot(rotationmat)

In [17]:
ind = 8

blick = np.loadtxt(root + "Blickfeld/point_cloud/%06d.csv" % ind,)
velo = np.loadtxt(root + "Velodyne/point_cloud/%06d.csv" % ind)
velo = transfer_points(velo.T[0:3], rotationmat).T

bb = np.loadtxt(root + "/Blickfeld/bounding_box/%06d.csv" % ind)
if len(bb):
    bb = make_boundingbox(bb)
else:
    bb = np.array([[None,None,None,None,None,None,None]])

In [18]:
data = [
        go.Scatter3d(x = velo[:,0],
                     y = velo[:,1],
                     z = velo[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(velo.shape[0]),
                    marker={
                        'size': 2,
                        'color': "green",
                        'colorscale':'rainbow',
}),
        go.Scatter3d(x = bb[:,0],
                     y = bb[:,1],
                     z = bb[:,2],
                     text=np.arange(8),
                    mode='markers', type='scatter3d',
                    marker={
                        'size': 2,
                        'color': "red",
                        'colorscale':'rainbow',
})
]
layout = go.Layout(
    scene={
        'xaxis': {'range': [-45, 45], 'rangemode': 'tozero', 'tick0': -5},
        'yaxis': {'range': [-45, 45], 'rangemode': 'tozero', 'tick0': -5},
        'zaxis': {'range': [-45, 45], 'rangemode': 'tozero'}
    }
)
go.Figure(data=data, layout = layout)

In [19]:
ind = 8
blick = np.loadtxt(root + "Blickfeld/point_cloud/%06d.csv" % ind,)
velo = np.loadtxt(root + "Velodyne/point_cloud/%06d.csv" % ind)
blick = transfer_points(blick.T[0:3], invrotationmat).T

bb = np.loadtxt(root + "/Velodyne/bounding_box/%06d.csv" % ind)
if len(bb):
    bb = make_boundingbox(bb)
else:
    bb = np.array([[None,None,None,None,None,None,None]])

In [20]:
data = [go.Scatter3d(x = blick[:,0],
                     y = blick[:,1],
                     z = blick[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(blick.shape[0]),
                    marker={
                        'size': 2,
                        'color': "blue",
                        'colorscale':'rainbow',
}),
        go.Scatter3d(x = velo[:,0],
                     y = velo[:,1],
                     z = velo[:,2],
                    mode='markers', type='scatter3d',
                    text=np.arange(velo.shape[0]),
                    marker={
                        'size': 2,
                        'color': "green",
                        'colorscale':'rainbow',
}),
        go.Scatter3d(x = bb[:,0],
                     y = bb[:,1],
                     z = bb[:,2],
                     text=np.arange(8),
                    mode='markers', type='scatter3d',
                    marker={
                        'size': 2,
                        'color': "red",
                        'colorscale':'rainbow',
})
]
layout = go.Layout(
    scene={
        'xaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'yaxis': {'range': [-25, 25], 'rangemode': 'tozero', 'tick0': -5},
        'zaxis': {'range': [-25, 25], 'rangemode': 'tozero'}
    }
)
go.Figure(data=data, layout = layout)